# Mini-Project 1 - Privacy

In this mini-project, you will design and implement differentially private algorithms for answering _epicenter queries_ on a twitter location dataset. 

**DUE:** Sep 23, noon (12pm)

**WHAT TO SUBMIT:** You should turn in your solution file (miniproject1_YOURUSERNAME.ipynb). Please complete all parts 1(a-b), 2(a-b), 3(a-b), 4(a-b), 5(a-b).  Pay attention to the 'TODO's.

**HOW TO SUBMIT:** Submit the file using LEARN (in upcoming events)(https://learn.uwaterloo.ca/d2l/home/492027).

In [ ]:
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.isotonic import IsotonicRegression  

You are given a set of tweets collected in western USA, denoted by $\mathbb{D}$. Each row in $\mathbb{D}$ is associated with a tweet and has the location information of this tweet. The location domain is discretized into a 2D grid of size 256 x 256. 

We preprocess this datset into a 2D matrix ('twitter.npy') that summarizes the number of tweets falling into each grid cell. We denote this matrix by D.

In [ ]:
D = np.load('twitter.npy') #load twitter.npy into a 256x256 numpy array
gridSize = D.shape
print(gridSize)
sns.heatmap(np.rot90(D), cmap="Blues", robust=True) #generate a heatmap of the 2D array

Your goal is to answer _epicenter queries_. An epicenter query $q(x,y,r,D)$ is defined by a grid cell center $(x,y)\in [0,256)\times [0,256)$ and a radius $r\in [0,256)$, and it reports a sequence of counts $[c_0, c_1 ,c_2  ...,c_i, ,...., c_r]$, where $c_i$ counts the number of tweets in the dataset $D$ falling into any grid cells $(x',y')$ at distance $\leq i$ from $(x,y)$, defined as $$c_i = \sum_{|x'-x|\leq i,|y'-y|\leq i} D[x',y'].$$

You are given 4 epicenter queries at 4 different grid cell centers with the same radius 20 as shown below.

In [ ]:
# Input to Epicenter Queries
r= 20
#Q1: 
x1=140
y1=140
#Q2:
x2=165
y2=170
#Q3
x3=200
y3=145
#Q4
x4=170
y4=115

## Task 1: 
(1a) Write a function to compute the true answer to an epicenter query q(x,y,r,D), where (x,y) is the center, r is the radius, D is the dataset (256x256 numpy array).

In [ ]:
def epicenterQuery(x,y,r,D):
    ans = np.zeros(r+1) #[c_0,c_1,...,c_r]
    #TODO: Add your code for computing the true answer to q(x,y,r,D)
    return ans

def plotAllQueryAns(ansArr):
    plt.plot(ansArr[0],'-g', label='Q1')
    plt.plot(ansArr[1],'--c', label='Q2')
    plt.plot(ansArr[2],'-.k', label='Q3')
    plt.plot(ansArr[3],':r', label='Q4')
    plt.legend();

ans1 = epicenterQuery(x1,y1,r,D) #Q1
ans2 = epicenterQuery(x2,y2,r,D) #Q2
ans3 = epicenterQuery(x3,y3,r,D) #Q3
ans4 = epicenterQuery(x4,y4,r,D) #Q4
trueAnsArr = [ans1,ans2,ans3,ans4]
plotAllQueryAns(trueAnsArr)


(1b) You will design $\epsilon$-differentially private algorithms for answering the four epicenter queries defined above. Each algorithm takes in a privacy budget $\epsilon$, and the database $D$, and returns $o_1,o_2,o_3,o_4$ as the output for the four queries respectively. We measure the error in the output as L2 norm of the difference between the noisy answers $o_1,o_2,o_3,o_4$ and the true answers $a_1,a_2,a_3,a_4$, i.e. 
$$\sqrt{\sum_{j=1}^4\sum_{i=0}^r (o_j[i]-a_j[i])^2}.$$ 

Complete the function below for computing the error. 

In [ ]:
def computeError(trueAnsArr, noisyAnsArr):
    error = 0.0
    #TODO: Add your code for computing the error
    return error

## Task 2:
(2a) Design an algorithm that first uses the Laplace mechanism to perturb the counts of all the grid cells and then uses the noisy counts for reporting the answers to the four epicenter queries.

In [ ]:
def lapMechanism(trueAns,epsilon,querySensitivity):
    noise = np.zeros(trueAns.shape) 
    noise = np.random.laplace(0,querySensitivity/epsilon,trueAns.shape)
    noisyAns = trueAns + noise
    return noisyAns

def algorithm1(D,epsilon):
    #Perturb the 2D matrix with Laplace Mechanism
    querySensitivity = 1000.0 #TODO: Update the query sensitivity 
    noisyD = lapMechanism(D, epsilon, querySensitivity)
    
    #Compute the noisy answer of the four queries using the noisyD
    noisyAns1 = epicenterQuery(x1,y1,r,noisyD)
    noisyAns2 = epicenterQuery(x2,y2,r,noisyD)
    noisyAns3 = epicenterQuery(x3,y3,r,noisyD)
    noisyAns4 = epicenterQuery(x4,y4,r,noisyD)
    return noisyD, [noisyAns1, noisyAns2, noisyAns3, noisyAns4]

#Testing your algorithm 
noisyD, noisyAnsArr_Algo1 = algorithm1(D, epsilon=0.1)
plotAllQueryAns(noisyAnsArr_Algo1)
error_Algo1 = computeError(trueAnsArr, noisyAnsArr_Algo1)
print(error_Algo1)

In [ ]:
sns.heatmap(np.rot90(noisyD), cmap="Blues",robust=True) #generate a heatmap of the noisy D

(2b) Show that Algorithm 1 is $\epsilon$-differentially private.

Proof: (TODO: Add your proof here. You can use Latex or Markdown)




## Task 3:
(3a) We have learnt in the class that post-processing query answers to satisfy constraints can improve accuracy. Can you design a new algorithm that post-processes the output of Algorithm 1 for better accuracy?

In [ ]:
def postprocess(noisyAns):
    noisyAnsPostprocess = np.zeros(noisyAns.size) 
    #TODO: Add code to process noisyAnsArr for better accuracy 
    #HINT: You may use http://scikit-learn.org/stable/auto_examples/plot_isotonic_regression.html
    return noisyAnsPostprocess

def algorithm2(D, epsilon):
    noisyD, noisyAnsArr_Algo1 = algorithm1(D, epsilon)
    noisyAnsArr_Algo2 = []
    for noisyAns in noisyAnsArr_Algo1:
        noisyAnsPostprocess = postprocess(noisyAns)
        noisyAnsArr_Algo2.append(noisyAnsPostprocess)
    return noisyAnsArr_Algo2

#Testing your algorithm 
noisyAnsArr_Algo2 = algorithm2(D, epsilon=0.1)
plotAllQueryAns(noisyAnsArr_Algo2)
error_Algo2 = computeError(trueAnsArr, noisyAnsArr_Algo2)
print(error_Algo2)

(3b) Show that Algorithm 2 is $\epsilon$-differentially private.

Proof: (TODO: ADD YOUR PROOF HERE)




## Task 4:
(4a) This part is open ended. Can you design an $\epsilon$-differentially private algorithm that answers the four queries with a smaller error than both algorithm 1 and algorithm 2? This new algorithm should be different from algorithm 1 and 2 in a non-trivial way.

In [ ]:
def algorithm3(D, epsilon):
    #TODO: Complete this algorithm
    noisyAns1 = 0.0 #noisy answer for epicenterQuery(x1,y1,r,D)
    noisyAns2 = 0.0 #noisy answer for epicenterQuery(x2,y2,r,D)
    noisyAns3 = 0.0 #noisy answer for epicenterQuery(x3,y3,r,D)
    noisyAns4 = 0.0 #noisy answer for epicenterQuery(x4,y4,r,D)

    return [noisyAns1, noisyAns2, noisyAns3, noisyAns4]

#Testing your algorithm 
noisyAnsArr_Algo3 = algorithm3(D, epsilon=0.1)
plotAllQueryAns(noisyAnsArr_Algo3)
error_Algo3 = computeError(trueAnsArr, noisyAnsArr_Algo3)
print(error_Algo3)

(4b) Show that Algorithm 3 designed by you is $\epsilon$-differentially private.

Proof: (TODO: ADD YOUR PROOF HERE)

## Task 5: 
(5a) Plot the means of L2 errors of 50 runs of Algorithm 1, Algorithm 2, and Algorithm 3 for privacy budget $\epsilon$ in {0.1, 0.2, 0.4, 0.8, 1.6} by running the code below. (No need to change the code.)

In [ ]:
epsilonArr = [0.1, 0.2, 0.4, 0.8, 1.6]
runs = 50
errorMeanArr_Algo1 = []
for epsilon in epsilonArr:
    errorEpsilon = []
    for i in range(runs):
        noisyD, noisyAnsArr_Algo1 = algorithm1(D, epsilon)
        error_Algo1 = computeError(trueAnsArr, noisyAnsArr_Algo1)  
        errorEpsilon.append(error_Algo1) 
    errorMeanArr_Algo1.append(np.mean(errorEpsilon))
    
errorMeanArr_Algo2 = []
for epsilon in epsilonArr:
    errorEpsilon = []
    for i in range(runs):
        noisyAnsArr_Algo2 = algorithm2(D, epsilon)
        error_Algo2 = computeError(trueAnsArr, noisyAnsArr_Algo2)  
        errorEpsilon.append(error_Algo2) 
    errorMeanArr_Algo2.append(np.mean(errorEpsilon))
    
errorMeanArr_Algo3 = []
for epsilon in epsilonArr:
    errorEpsilon = []
    for i in range(runs):
        noisyAnsArr_Algo3 = algorithm3(D, epsilon)
        error_Algo3 = computeError(trueAnsArr, noisyAnsArr_Algo3)  
        errorEpsilon.append(error_Algo3) 
    errorMeanArr_Algo3.append(np.mean(errorEpsilon))

plt.plot(epsilonArr,errorMeanArr_Algo1,'-g', label='Algo1')
plt.plot(epsilonArr,errorMeanArr_Algo2,'--c', label='Algo2')
plt.plot(epsilonArr,errorMeanArr_Algo3,'-.k', label='Algo3')
plt.legend();

(5b) Describe and explain the trends in these plots respectively. 

Your Answer: